## Installations

In [3]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import pyranges as pr
import seaborn as sns
import xarray as xr

# Seaborn customisation
sns.set_theme()
sns.set_style("whitegrid")
biomodal_palette = ["#003B49", "#9CDBD9", "#F87C56", "#C0DF16", "#05868E"]
sns.set_palette(biomodal_palette)

from modality.datasets import load_biomodal_dataset
from modality.annotation import (
    get_genes,
    get_transcription_end_region,
    get_tss_region,
    get_exons,
    get_introns,
    get_five_prime_utrs,
    get_three_prime_utrs,
    get_transcripts,
    get_cpg_islands,
)

Load ES-E14 evoC dataset

In [2]:
from modality.contig_dataset import ContigDataset
def load_data():
    #downloads modality.contig_dataset.ContigDataset object
    ds = load_biomodal_dataset()
    # ds = ContigDataset.from_zarrz("../ES-E14.zarrz")
    ds = ds.drop_vars(["Input DNA Quantity (ng/sample)", "tech_replicate_number"])  
    ds = ds.sum(dim="sample_id", keep_attrs=True)
    ds = ds.expand_dims(dim="sample_id", axis=1)
    ds = ds.assign_coords(sample_id=["sample_0"])
    ds.assign_fractions(
        numerators=["num_modc", "num_mc", "num_hmc"],
        denominator="num_total_c",
        min_coverage=10,
        inplace=True,
    )
    return ds

ds = load_data()

2024-08-06 12:16:11 | INFO | [modality/read_locally.py:32] Staging file gs://quant2zarr-artefacts/esE14/v1.0/metadata.csv from GCS
2024-08-06 12:16:11 | INFO | [modality/read_locally.py:32] Staging file gs://quant2zarr-artefacts/esE14/v1.0/quant-to-zarr_1.0.0_esE14_release_evoC_njh_2024-02-22-17-20-16/zarr/CG/esE14_release_evoC_CG.zarrz from GCS
2024-08-06 12:16:12 | WARNING | [modality/contig_dataset.py:340] "sample_id" coordinate is missing but expected to be set by many ContigDataset methods.
It can be added using the `assign_coords` method, e.g. `ds.assign_coords(sample_id = ("sample_id", ["sample1", "sample2"]))`
2024-08-06 12:16:12 | WARNING | [modality/contig_dataset.py:340] "sample_id" coordinate is missing but expected to be set by many ContigDataset methods.
It can be added using the `assign_coords` method, e.g. `ds.assign_coords(sample_id = ("sample_id", ["sample1", "sample2"]))`


#### subset `ContigDataset` by strand

In [4]:
from modality.contig_dataset import set_contig_slices, cast_result

def refresh_slices(subset_data):
    if subset_data.pos.size == 0:
            raise ValueError(
                "Subset is empty. Please check the coverage values and method used."
            )
    else:
        slices = [x for x in subset_data.attrs if x.startswith("slice")]
        for sl in slices:
            subset_data.attrs.pop(sl)

        return set_contig_slices(subset_data)

def split_strand(data, strand):
    """
    split xarray dataset into positive and negative strands
    Parameters
        data : xarray.Dataset
        strand : str ('+', '-')
    Returns
        strand_data :xarray.Dataset
    """
    strand_mask = (data['strand'].data == strand).compute()
    masked_da = xr.DataArray(strand_mask, dims=data['strand'].dims, coords=data['strand'].coords)
    strand_data = data.where(masked_da, drop=True)

    return cast_result(refresh_slices(strand_data.ds))

plus_strand = split_strand(ds, "+")
minus_strand = split_strand(ds, "-")

2024-08-06 12:24:41 | INFO | [modality/contig_slices.py:25] Computing available chromosomes.
2024-08-06 12:24:41 | INFO | [modality/contig_slices.py:44] Found available contigs: 1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,X,Y,MT.
2024-08-06 12:25:04 | INFO | [modality/contig_slices.py:25] Computing available chromosomes.
2024-08-06 12:25:04 | INFO | [modality/contig_slices.py:44] Found available contigs: 1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,X,Y,MT.


In [5]:
plus_strand

ContigDataset(data_vars=Data variables:
    num_c        (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    num_hmc      (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    num_mc       (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    num_modc     (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    num_other    (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    num_total    (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    num_total_c  (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    frac_modc    (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    frac_mc      (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    frac_hmc     (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>, coords=Coordinates:
    contig        (pos) <U5 dask.array<chunksize=(50000,), meta=np.ndarray>
    ref_position  (pos) int64 dask.array<chunksize=(50000,), meta=np.ndarray>
    strand        (pos) <U2 dask.array<chunksize=(50000,), meta=np.ndarray>
  * sample_id     (sample_id) <U8 'sample_0'
    group         (sample_id) <U8 'sample_0', attrs={'context': 'CG', 'context_sampling': 1.0, 'contigs': ['1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', 'X', 'Y', 'MT'], 'coordinate_basis': 0, 'description': 'An evoC dataset of mouse ES-E14 cells, data contains 4 technical replicates.\nThese data aligned to the mm38 genome.', 'fasta_path': 'GRCm38-ss-ctrls-v23.fa.gz', 'frac_denominator': 'num_total_c', 'frac_min_coverage': 10, 'input_path': ['CEG1485-EL01-D1115-001.genome.GRCm38.dedup.duet-modC.CG_quant.tsv.gz', 'CEG1485-EL01-D1115-002.genome.GRCm38.dedup.duet-modC.CG_quant.tsv.gz', 'CEG1485-EL01-D1115-003.genome.GRCm38.dedup.duet-modC.CG_quant.tsv.gz', 'CEG1485-EL01-D1115-004.genome.GRCm38.dedup.duet-modC.CG_quant.tsv.gz'], 'quant_type': 'quant6L', 'ref_name': 'GRCm38', 'sample_ids': ['CEG1485-EL01-D1115-001', 'CEG1485-EL01-D1115-002', 'CEG1485-EL01-D1115-003', 'CEG1485-EL01-D1115-004'], 'slice_1': slice(0, 868704, 1), 'slice_10': slice(6973201, 7655712, 1), 'slice_11': slice(7655712, 8424647, 1), 'slice_12': slice(8424647, 9002865, 1), 'slice_13': slice(9002865, 9598341, 1), 'slice_14': slice(9598341, 10160405, 1), 'slice_15': slice(10160405, 10705365, 1), 'slice_16': slice(10705365, 11159809, 1), 'slice_17': slice(11159809, 11693082, 1), 'slice_18': slice(11693082, 12139087, 1), 'slice_19': slice(12139087, 12505171, 1), 'slice_2': slice(868704, 1831040, 1), 'slice_3': slice(1831040, 2521902, 1), 'slice_4': slice(2521902, 3323979, 1), 'slice_5': slice(3323979, 4160524, 1), 'slice_6': slice(4160524, 4857217, 1), 'slice_7': slice(4857217, 5576860, 1), 'slice_8': slice(5576860, 6302520, 1), 'slice_9': slice(6302520, 6973201, 1), 'slice_MT': slice(13036853, 13037140, 1), 'slice_X': slice(12505171, 12880337, 1), 'slice_Y': slice(12880337, 13036853, 1)})

In [6]:
minus_strand

ContigDataset(data_vars=Data variables:
    num_c        (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    num_hmc      (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    num_mc       (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    num_modc     (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    num_other    (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    num_total    (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    num_total_c  (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    frac_modc    (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    frac_mc      (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>
    frac_hmc     (pos, sample_id) float64 dask.array<chunksize=(50000, 1), meta=np.ndarray>, coords=Coordinates:
    contig        (pos) <U5 dask.array<chunksize=(50000,), meta=np.ndarray>
    ref_position  (pos) int64 dask.array<chunksize=(50000,), meta=np.ndarray>
    strand        (pos) <U2 dask.array<chunksize=(50000,), meta=np.ndarray>
  * sample_id     (sample_id) <U8 'sample_0'
    group         (sample_id) <U8 'sample_0', attrs={'context': 'CG', 'context_sampling': 1.0, 'contigs': ['1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', 'X', 'Y', 'MT'], 'coordinate_basis': 0, 'description': 'An evoC dataset of mouse ES-E14 cells, data contains 4 technical replicates.\nThese data aligned to the mm38 genome.', 'fasta_path': 'GRCm38-ss-ctrls-v23.fa.gz', 'frac_denominator': 'num_total_c', 'frac_min_coverage': 10, 'input_path': ['CEG1485-EL01-D1115-001.genome.GRCm38.dedup.duet-modC.CG_quant.tsv.gz', 'CEG1485-EL01-D1115-002.genome.GRCm38.dedup.duet-modC.CG_quant.tsv.gz', 'CEG1485-EL01-D1115-003.genome.GRCm38.dedup.duet-modC.CG_quant.tsv.gz', 'CEG1485-EL01-D1115-004.genome.GRCm38.dedup.duet-modC.CG_quant.tsv.gz'], 'quant_type': 'quant6L', 'ref_name': 'GRCm38', 'sample_ids': ['CEG1485-EL01-D1115-001', 'CEG1485-EL01-D1115-002', 'CEG1485-EL01-D1115-003', 'CEG1485-EL01-D1115-004'], 'slice_1': slice(0, 868704, 1), 'slice_10': slice(6973201, 7655712, 1), 'slice_11': slice(7655712, 8424647, 1), 'slice_12': slice(8424647, 9002865, 1), 'slice_13': slice(9002865, 9598341, 1), 'slice_14': slice(9598341, 10160405, 1), 'slice_15': slice(10160405, 10705365, 1), 'slice_16': slice(10705365, 11159809, 1), 'slice_17': slice(11159809, 11693082, 1), 'slice_18': slice(11693082, 12139087, 1), 'slice_19': slice(12139087, 12505171, 1), 'slice_2': slice(868704, 1831040, 1), 'slice_3': slice(1831040, 2521902, 1), 'slice_4': slice(2521902, 3323979, 1), 'slice_5': slice(3323979, 4160524, 1), 'slice_6': slice(4160524, 4857217, 1), 'slice_7': slice(4857217, 5576860, 1), 'slice_8': slice(5576860, 6302520, 1), 'slice_9': slice(6302520, 6973201, 1), 'slice_MT': slice(13036853, 13037140, 1), 'slice_X': slice(12505171, 12880337, 1), 'slice_Y': slice(12880337, 13036853, 1)})

#### Loading mm10 (GRCm38) reference genome from [GENCODE](https://www.gencodegenes.org/)

In [7]:
# Get the gene annotations
gene_filter = {
    "gene_type": "protein_coding",
    "source": "HAVANA",
}

genes = get_genes(
    reference="mm10",
    as_pyranges=True,
    filterby=gene_filter,
)
print(genes.head(5))

# Get transcripts for mm10
transcripts = get_transcripts(
        reference="mm10",
        contig=None,
        start=None,
        end=None,
        as_pyranges=False,
    )

print('-'*100)

print(f" all genes: {len(genes)}")
print(f" unique gene id: {len(genes.df['Id'])}")


2024-08-06 12:29:33 | INFO | [modality/annotation.py:418] Removing readthrough_gene transcripts for gff (https://ftp.ebi.ac.uk/pub/databases/gencode/Gencode_mouse/release_M25/gencode.vM25.basic.annotation.gff3.gz)
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}


+--------------+------------+------------+-----------+-----------+-------+
|   Chromosome | Source     | Type       |     Start |       End | +12   |
|   (category) | (object)   | (object)   |   (int64) |   (int64) | ...   |
|--------------+------------+------------+-----------+-----------+-------|
|            1 | HAVANA     | gene       |   4807787 |   4848409 | ...   |
|            1 | HAVANA     | gene       |   4807891 |   4886769 | ...   |
|            1 | HAVANA     | gene       |   4857813 |   4897908 | ...   |
|            1 | HAVANA     | gene       |   5070017 |   5162528 | ...   |
|            1 | HAVANA     | gene       |   5588465 |   5606130 | ...   |
+--------------+------------+------------+-----------+-----------+-------+
Stranded PyRanges object has 5 rows and 17 columns from 1 chromosomes.
For printing, the PyRanges was sorted on Chromosome and Strand.
12 hidden columns: Score, Strand, Phase, Id, Gene_id, Gene_type, Gene_name, Level, ... (+ 4 more.)


2024-08-06 12:29:39 | INFO | [modality/annotation.py:418] Removing readthrough_gene transcripts for gff (https://ftp.ebi.ac.uk/pub/databases/gencode/Gencode_mouse/release_M25/gencode.vM25.basic.annotation.gff3.gz)


----------------------------------------------------------------------------------------------------
 all genes: 21673
 unique gene id: 21673


#### Select primiary transcript for each gene

In [9]:
def select_transcript_based_on_tag(df):
    # for each transcript in df, select the one with the highest priority tag
    # priorities are:
        # 1. 'basic,appris_principal_1,CCDS'
        # 2. 'basic,appris_principal_1'
        # 3. 'basic,CCDS'
        # 4. 'basic'
    # but with 'exp_conf' (experimentally confirmed) tag, the priority is higher.
    
    priorties = {
        'basic,appris_principal_1,exp_conf,CCDS': 1,
        'basic,appris_principal_1,CCDS': 1,
        'basic,appris_principal_1,exp_conf': 3,
        'basic,appris_principal_1': 4,
        'basic,exp_conf,CCDS': 5,
        'basic,CCDS': 6,
        'basic,exp_conf': 7,
        'basic': 8
    }

    # sort the dataframe by the priority of the tags
    df['tag_priority'] = df.tag.map(priorties)

    df = df.sort_values(by='tag_priority')

    # drop duplicates, keeping the first one
    df = df.drop_duplicates(subset='gene_id', keep='first')

    return df[["gene_id", "transcript_id"]]

selected_transcripts = transcripts.groupby('gene_id').apply(
    select_transcript_based_on_tag
    ).reset_index(drop=True)
selected_transcripts.head()

/var/folders/gg/n2wtdbl13m54f9xcjyl_k3qr0000gp/T/ipykernel_97790/2121809373.py:31: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  selected_transcripts = transcripts.groupby('gene_id').apply(


gene_id          transcript_id
0   ENSMUSG00000000001.4   ENSMUST00000000001.4
1  ENSMUSG00000000003.15  ENSMUST00000000003.13
2  ENSMUSG00000000028.15  ENSMUST00000000028.13
3  ENSMUSG00000000037.17   ENSMUST00000101113.8
4  ENSMUSG00000000049.11   ENSMUST00000000049.5

In [10]:
# Create dictionary for gene_id to transcript_id mapping
gene_to_transcription = selected_transcripts.set_index('gene_id')['transcript_id'].to_dict()
print(f"There are {len(gene_to_transcription)} genes with unique transcript ids")

There are 21541 genes with unique transcript ids


review / drop genes with no transcripts

In [11]:
# Function to map transcription_id
def map_transcription_id(gene_id, gene_to_transcription):
    return gene_to_transcription.get(gene_id, None)

# Map transcription_id 
genes_df = genes.df
genes_df['Transcript_id'] = genes_df['Gene_id'].map(lambda gene_id: map_transcription_id(gene_id, gene_to_transcription))
genes_clean = pr.PyRanges(genes_df)

# Find and Handle missing gene_ids
missing_gene_ids = genes_clean.df[genes_clean.df['Transcript_id'].isna()]['Gene_id'].tolist()
missing_df = genes_clean.df[genes_clean.df['Gene_id'].isin(missing_gene_ids)]
genes_clean = genes_clean[~genes_clean.df['Transcript_id'].isna()]
print(f"all genes: {len(genes)}")
print(f"all genes with annotated transcripts: {len(genes_clean)}")
genes_clean

/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:160: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  empty_removed = df.groupby(["Chromosome", "Strand"])


all genes: 21673
all genes with annotated transcripts: 21541


+--------------+------------+------------+-----------+-----------+-------+
| Chromosome   | Source     | Type       | Start     | End       | +13   |
| (category)   | (object)   | (object)   | (int64)   | (int64)   | ...   |
|--------------+------------+------------+-----------+-----------+-------|
| 1            | HAVANA     | gene       | 4807787   | 4848409   | ...   |
| 1            | HAVANA     | gene       | 4807891   | 4886769   | ...   |
| 1            | HAVANA     | gene       | 4857813   | 4897908   | ...   |
| 1            | HAVANA     | gene       | 5070017   | 5162528   | ...   |
| ...          | ...        | ...        | ...       | ...       | ...   |
| Y            | HAVANA     | gene       | 79148788  | 79151121  | ...   |
| Y            | HAVANA     | gene       | 84562571  | 84564906  | ...   |
| Y            | HAVANA     | gene       | 85528516  | 85530907  | ...   |
| Y            | HAVANA     | gene       | 89713423  | 89745531  | ...   |
+--------------+------------+------------+-----------+-----------+-------+
Stranded PyRanges object has 21,541 rows and 18 columns from 21 chromosomes.
For printing, the PyRanges was sorted on Chromosome and Strand.
13 hidden columns: Score, Strand, Phase, Id, Gene_id, Gene_type, Gene_name, Level, ... (+ 5 more.)

In [12]:
print(f"Tags for {len(missing_df)} missing genes:")
print(missing_df['Tag'].value_counts())

Tags for 132 missing genes:
Tag
                                                 87
overlapping_locus                                13
reference_genome_error                           10
fragmented_locus                                  9
ncRNA_host,fragmented_locus                       2
ncRNA_host                                        2
overlapping_locus,reference_genome_error          2
ncRNA_host,reference_genome_error                 2
ncRNA_host,overlapping_locus                      2
fragmented_locus,reference_genome_error           1
fragmented_locus,overlapping_locus                1
ncRNA_host,fragmented_locus,overlapping_locus     1
Name: count, dtype: int64


## Extract Regions

### requires stitching

#### 200bp before Transcription Start Site

In [16]:
# default arguments for get_tss_region and get_transcription_end_region
default_args = {
    "contig": None,
    "start": None,
    "end": None,
    "reference": "mm10",
    "as_pyranges": True,
    "protein_coding": True,
    "filterby": None,
}

In [15]:
before_tss = get_tss_region(
    start_offset=-200,
    span=200,
    **default_args,
)

# Map transcription_id 
before_tss_df = before_tss.df
before_tss_df['Transcript_id'] = before_tss_df['Gene_id'].map(lambda gene_id: map_transcription_id(gene_id, gene_to_transcription))
before_tss = pr.PyRanges(before_tss_df)
before_tss = before_tss[~before_tss.df['Transcript_id'].isna()]

print(f"before_tss regions with transcripts: {len(before_tss)}")
print("="*100)

2024-08-06 12:59:24 | INFO | [modality/annotation.py:418] Removing readthrough_gene transcripts for gff (https://ftp.ebi.ac.uk/pub/databases/gencode/Gencode_mouse/release_M25/gencode.vM25.basic.annotation.gff3.gz)


before_tss regions with transcripts: 21541


/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:160: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass o

In [22]:
#split strands
before_tss_plus = pr.PyRanges(before_tss.df[before_tss.df["Strand"]=="+"])
before_tss_minus = pr.PyRanges(before_tss.df[before_tss.df["Strand"]=="-"])

before_tss_plus = before_tss_plus.unstrand()
before_tss_minus = before_tss_minus.unstrand()
before_tss_plus

/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}


+--------------+------------+------------+-----------+-----------+-------+
| Chromosome   | Source     | Type       | Start     | End       | +12   |
| (category)   | (object)   | (object)   | (int64)   | (int64)   | ...   |
|--------------+------------+------------+-----------+-----------+-------|
| 1            | HAVANA     | gene       | 4807587   | 4807787   | ...   |
| 1            | HAVANA     | gene       | 4807691   | 4807891   | ...   |
| 1            | HAVANA     | gene       | 4857613   | 4857813   | ...   |
| 1            | HAVANA     | gene       | 5069817   | 5070017   | ...   |
| ...          | ...        | ...        | ...       | ...       | ...   |
| Y            | HAVANA     | gene       | 87550765  | 87550965  | ...   |
| Y            | HAVANA     | gene       | 88053114  | 88053314  | ...   |
| Y            | HAVANA     | gene       | 89052605  | 89052805  | ...   |
| Y            | HAVANA     | gene       | 90401047  | 90401247  | ...   |
+--------------+------------+------------+-----------+-----------+-------+
Unstranded PyRanges object has 10,740 rows and 17 columns from 21 chromosomes.
For printing, the PyRanges was sorted on Chromosome.
12 hidden columns: Score, Phase, Id, Gene_id, Gene_type, Gene_name, Level, Mgi_id, ... (+ 4 more.)

#### 1000bp after Transcription End Site

In [17]:
after_tes = get_transcription_end_region(
    start_offset=0,
    span=1000,
    **default_args,
)

# Map transcription_id 
after_tes_df = after_tes.df
after_tes_df['Transcript_id'] = after_tes_df['Gene_id'].map(lambda gene_id: map_transcription_id(gene_id, gene_to_transcription))
after_tes = pr.PyRanges(before_tss_df)
after_tes = after_tes[~after_tes.df['Transcript_id'].isna()]

print(f"after_tes regions with transcripts: {len(after_tes)}")
print("="*100)

2024-08-06 13:01:22 | INFO | [modality/annotation.py:418] Removing readthrough_gene transcripts for gff (https://ftp.ebi.ac.uk/pub/databases/gencode/Gencode_mouse/release_M25/gencode.vM25.basic.annotation.gff3.gz)


after_tes regions with transcripts: 21541


/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:160: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass o

In [21]:
#split strands
after_tes_plus = pr.PyRanges(after_tes.df[after_tes.df["Strand"]=="+"])
after_tes_minus = pr.PyRanges(after_tes.df[after_tes.df["Strand"]=="-"])

after_tes_plus = after_tes_plus.unstrand()
after_tes_minus = after_tes_minus.unstrand()
after_tes_plus

/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}


+--------------+------------+------------+-----------+-----------+-------+
| Chromosome   | Source     | Type       | Start     | End       | +12   |
| (category)   | (object)   | (object)   | (int64)   | (int64)   | ...   |
|--------------+------------+------------+-----------+-----------+-------|
| 1            | HAVANA     | gene       | 4807587   | 4807787   | ...   |
| 1            | HAVANA     | gene       | 4807691   | 4807891   | ...   |
| 1            | HAVANA     | gene       | 4857613   | 4857813   | ...   |
| 1            | HAVANA     | gene       | 5069817   | 5070017   | ...   |
| ...          | ...        | ...        | ...       | ...       | ...   |
| Y            | HAVANA     | gene       | 87550765  | 87550965  | ...   |
| Y            | HAVANA     | gene       | 88053114  | 88053314  | ...   |
| Y            | HAVANA     | gene       | 89052605  | 89052805  | ...   |
| Y            | HAVANA     | gene       | 90401047  | 90401247  | ...   |
+--------------+------------+------------+-----------+-----------+-------+
Unstranded PyRanges object has 10,740 rows and 17 columns from 21 chromosomes.
For printing, the PyRanges was sorted on Chromosome.
12 hidden columns: Score, Phase, Id, Gene_id, Gene_type, Gene_name, Level, Mgi_id, ... (+ 4 more.)

#### Extract 3`UTRs

In [24]:
# extract with modality.get_three_prime_utrs
three_prime_utrs = get_three_prime_utrs(reference="mm10")
three_prime_utrs = three_prime_utrs[
    three_prime_utrs.Transcript_id.isin(selected_transcripts.transcript_id)
    ]

#split strands
three_prime_utrs_plus = pr.PyRanges(three_prime_utrs.df[three_prime_utrs.df["Strand"]=="+"])
three_prime_utrs_plus = three_prime_utrs_plus.unstrand()

three_prime_utrs_minus = pr.PyRanges(three_prime_utrs.df[three_prime_utrs.df["Strand"]=="-"])
three_prime_utrs_minus = three_prime_utrs_minus.unstrand()

print(f"strand shape: + {three_prime_utrs_plus.df.shape}, - {three_prime_utrs_minus.df.shape}")
three_prime_utrs_plus

2024-08-06 13:10:51 | INFO | [modality/annotation.py:418] Removing readthrough_gene transcripts for gff (https://ftp.ebi.ac.uk/pub/databases/gencode/Gencode_mouse/release_M25/gencode.vM25.basic.annotation.gff3.gz)
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}


strand shape: + (8075, 27), - (8134, 27)


/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}


+--------------+------------+-----------------+-----------+-------+
| Chromosome   | Source     | Type            | Start     | +23   |
| (category)   | (object)   | (object)        | (int64)   | ...   |
|--------------+------------+-----------------+-----------+-------|
| 1            | HAVANA     | three_prime_UTR | 4845016   | ...   |
| 1            | HAVANA     | three_prime_UTR | 4896364   | ...   |
| 1            | HAVANA     | three_prime_UTR | 5602784   | ...   |
| 1            | HAVANA     | three_prime_UTR | 6274275   | ...   |
| ...          | ...        | ...             | ...       | ...   |
| Y            | HAVANA     | three_prime_UTR | 86087758  | ...   |
| Y            | HAVANA     | three_prime_UTR | 87142720  | ...   |
| Y            | HAVANA     | three_prime_UTR | 87575495  | ...   |
| Y            | HAVANA     | three_prime_UTR | 88079297  | ...   |
+--------------+------------+-----------------+-----------+-------+
Unstranded PyRanges object has 8,075 rows and 27 columns from 21 chromosomes.
For printing, the PyRanges was sorted on Chromosome.
23 hidden columns: End, Score, Phase, Id, Parent, Gene_id, Transcript_id, ... (+ 16 more.)

#### Extract 5`UTRs

In [25]:
# extract with modality.get_five_prime_utrs
five_prime_utrs = get_five_prime_utrs(reference="mm10")
five_prime_utrs = five_prime_utrs[
    five_prime_utrs.Transcript_id.isin(selected_transcripts.transcript_id)
    ]

#split strands
five_prime_utrs_plus = pr.PyRanges(five_prime_utrs.df[five_prime_utrs.df["Strand"]=="+"])
five_prime_utrs_plus = five_prime_utrs_plus.unstrand()

five_prime_utrs_minus = pr.PyRanges(five_prime_utrs.df[five_prime_utrs.df["Strand"]=="-"])
five_prime_utrs_minus = five_prime_utrs_minus.unstrand()
print(f"strand shape: + {five_prime_utrs_plus.df.shape}, - {five_prime_utrs_minus.df.shape}")
five_prime_utrs_plus

2024-08-06 13:12:35 | INFO | [modality/annotation.py:418] Removing readthrough_gene transcripts for gff (https://ftp.ebi.ac.uk/pub/databases/gencode/Gencode_mouse/release_M25/gencode.vM25.basic.annotation.gff3.gz)
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
/Users/nicol

strand shape: + (11449, 27), - (11369, 27)


+--------------+------------+----------------+-----------+-------+
| Chromosome   | Source     | Type           | Start     | +23   |
| (category)   | (object)   | (object)       | (int64)   | ...   |
|--------------+------------+----------------+-----------+-------|
| 1            | HAVANA     | five_prime_UTR | 4807822   | ...   |
| 1            | HAVANA     | five_prime_UTR | 4857813   | ...   |
| 1            | HAVANA     | five_prime_UTR | 5588492   | ...   |
| 1            | HAVANA     | five_prime_UTR | 5589034   | ...   |
| ...          | ...        | ...            | ...       | ...   |
| Y            | HAVANA     | five_prime_UTR | 87550965  | ...   |
| Y            | HAVANA     | five_prime_UTR | 87552378  | ...   |
| Y            | HAVANA     | five_prime_UTR | 88053314  | ...   |
| Y            | HAVANA     | five_prime_UTR | 88054723  | ...   |
+--------------+------------+----------------+-----------+-------+
Unstranded PyRanges object has 11,449 rows and 27 columns from 21 chromosomes.
For printing, the PyRanges was sorted on Chromosome.
23 hidden columns: End, Score, Phase, Id, Parent, Gene_id, Transcript_id, ... (+ 16 more.)

#### Extract exons and introns

In [27]:
# Exons:
exons = get_exons(reference="mm10")
exons = exons[exons.Transcript_id.isin(selected_transcripts.transcript_id)]

# exons split strands
exons_plus = pr.PyRanges(exons.df[exons.df["Strand"]=="+"])
first_exons_plus = exons_plus[exons_plus.Exon_number == "1"].unstrand()
exons_plus = exons_plus[exons_plus.Exon_number.astype("int") > 1].unstrand()


exons_minus = pr.PyRanges(exons.df[exons.df["Strand"]=="-"])
first_exons_minus = exons_minus[exons_minus.Exon_number == "1"].unstrand()
exons_minus = exons_minus[exons_minus.Exon_number.astype("int") > 1].unstrand()

2024-08-06 13:22:15 | INFO | [modality/annotation.py:418] Removing readthrough_gene transcripts for gff (https://ftp.ebi.ac.uk/pub/databases/gencode/Gencode_mouse/release_M25/gencode.vM25.basic.annotation.gff3.gz)
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
/Users/nicol

In [26]:
#Introns:
introns = get_introns(
    reference="mm10",
    transcripts=selected_transcripts.transcript_id.values,
    nb_workers=8,
)

# introns split strands
introns_plus = pr.PyRanges(introns.df[introns.df["Strand"]=="+"])
first_introns_plus = introns_plus[introns_plus.Intron_number == "1"].unstrand()
introns_plus = introns_plus[introns_plus.Intron_number.astype("int") > 1].unstrand()


introns_minus = pr.PyRanges(introns.df[introns.df["Strand"]=="-"])
first_introns_minus = introns_minus[introns_minus.Intron_number == "1"].unstrand()
introns_minus = introns_minus[introns_minus.Intron_number.astype("int") > 1].unstrand()



2024-08-06 13:18:13 | INFO | [modality/annotation.py:418] Removing readthrough_gene transcripts for gff (https://ftp.ebi.ac.uk/pub/databases/gencode/Gencode_mouse/release_M25/gencode.vM25.basic.annotation.gff3.gz)
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
2024-08-06 13:18:24 | INFO | [modality/annotation.py:418] Removing readthrough_gene transcripts for gff (https://ftp.ebi.ac.uk/pub/databases/gencode/Gencode_mouse/release_M25/gencode.vM25.basic.annotation.gff3.gz)
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to Tr

INFO: Pandarallel will run on 8 workers.
INFO: Pandarallel will use standard multiprocessing data transfer (pipe) to transfer data between the main process and workers.


/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  return {k: v for k, v in df.groupby(grpby_key)}
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass ob

In [28]:
print(f"Exons strand shape: + {exons_plus.df.shape}, - {exons_minus.df.shape}")
print(f"Introns strand shape: + {introns_plus.df.shape}, - {introns_minus.df.shape}")

print(f"First Exons strand shape: + {first_exons_plus.df.shape}, - {first_exons_minus.df.shape}")
print(f"First Introns strand shape: + {first_introns_plus.df.shape}, - {first_introns_minus.df.shape}")

Exons strand shape: + (90807, 27), - (90167, 27)
Introns strand shape: + (85982, 20), - (85480, 20)
First Exons strand shape: + (10740, 27), - (10801, 27)
First Introns strand shape: + (10186, 20), - (10212, 20)


In [29]:
print(exons.columns) # get_exons don't return "Transcript_support_level", 'Havana_transcript', 'Protein_id', 'Ccdsid', 'Ont', 'Parent', 'Exon_id', 'Exon_number'
print(introns.columns) # get_introns specific fields return 'Level_1'

Index(['Chromosome', 'Source', 'Type', 'Start', 'End', 'Score', 'Strand',
       'Phase', 'Id', 'Parent', 'Gene_id', 'Transcript_id', 'Gene_type',
       'Gene_name', 'Transcript_type', 'Transcript_name', 'Exon_number',
       'Exon_id', 'Level', 'Transcript_support_level', 'Mgi_id', 'Tag',
       'Havana_gene', 'Havana_transcript', 'Protein_id', 'Ccdsid', 'Ont',
       'Ranges_ID'],
      dtype='object')
Index(['Transcript_id', 'Level_1', 'Chromosome', 'Source', 'Type', 'Start',
       'End', 'Score', 'Strand', 'Phase', 'Id', 'Gene_id', 'Gene_type',
       'Gene_name', 'Level', 'Mgi_id', 'Havana_gene', 'Tag', 'Ranges_id',
       'Intron_number', 'Ranges_ID'],
      dtype='object')


#### Summarise 3\` 5\` UTRs exons and introns regions

In [31]:
def get_mean_across_region(df, var):
    sum_var = df[f"{var}_sum"].sum()
    sum_total_c = df["num_total_c_sum"].sum()
    return sum_var / sum_total_c
def summarise_across_region(rdr, region):
    """
    Summarise the methylation data across a region.

    Parameters
        rdr: pyranges object
        region: str

    Returns
        grouped_df: pd.DataFrame
    """

    df = rdr.to_dataframe().reset_index(level="sample_id", drop=True)
    grouped = df.groupby("Gene_id")

    mean_mc = grouped.apply(get_mean_across_region, var="num_mc")
    mean_hmc = grouped.apply(get_mean_across_region, var="num_hmc")
    mean_modc = grouped.apply(get_mean_across_region, var="num_modc")
    cpg_count = grouped["num_total_c_cpg_count"].sum()
    range_length = grouped["range_length"].sum()
    gene_name = grouped["Gene_name"].first()
    contig = grouped["contig"].first()
    strand = grouped["strand"].first()
    
    
    # Prepare list for storing primary_transcripts and handling missing gene_ids
    primary_transcripts = []
    missing_gene_ids = []

    for gene_id in grouped.groups.keys():
        if gene_id in gene_to_transcription:
            primary_transcripts.append(gene_to_transcription[gene_id])
        else:
            primary_transcripts.append(None)
            missing_gene_ids.append(gene_id)

    # Print missing gene_ids
    for gene_id in missing_gene_ids:
        print(f"Gene_ID {gene_id} not found in selected_transcripts")

    
    grouped_df = pd.DataFrame(
        {
            "mean_mc": mean_mc,
            "mean_hmc": mean_hmc,
            "mean_modc": mean_modc,
            "cpg_count": cpg_count,
            "range_length": range_length,
            "Gene_name": gene_name,
            "contig": contig,
            "strand": strand,
            "Transcript_id": primary_transcripts,
        }
    )

    grouped_df = grouped_df.reset_index()
    grouped_df["Region"] = region
    return grouped_df

In [32]:
dict_regions_to_patch_plus = {
    "exons": exons_plus,
    "introns": introns_plus,
    "five_prime_utrs": five_prime_utrs_plus,
    "three_prime_utrs": three_prime_utrs_plus,
}

dict_regions_to_patch_minus = {
    "exons": exons_minus,
    "introns": introns_minus,
    "five_prime_utrs": five_prime_utrs_minus,
    "three_prime_utrs": three_prime_utrs_minus,
}

dict_regions_to_patch_plus

{'exons': +--------------+------------+------------+-----------+-----------+-------+
 | Chromosome   | Source     | Type       | Start     | End       | +22   |
 | (category)   | (object)   | (object)   | (int64)   | (int64)   | ...   |
 |--------------+------------+------------+-----------+-----------+-------|
 | 1            | HAVANA     | exon       | 4808454   | 4808485   | ...   |
 | 1            | HAVANA     | exon       | 4828583   | 4828648   | ...   |
 | 1            | HAVANA     | exon       | 4828583   | 4828648   | ...   |
 | 1            | HAVANA     | exon       | 4830267   | 4830314   | ...   |
 | ...          | ...        | ...        | ...       | ...       | ...   |
 | Y            | HAVANA     | exon       | 90429592  | 90429709  | ...   |
 | Y            | HAVANA     | exon       | 90430460  | 90430559  | ...   |
 | Y            | HAVANA     | exon       | 90432572  | 90432670  | ...   |
 | Y            | HAVANA     | exon       | 90433029  | 90433262  | ...   |
 +-

Build sense and antisense methylation summary

In [33]:
def summarise_methylation_across_regions(plus_strand_cpgs, minus_strand_cpgs, regions_dict, region_strand, sense_methylation={}, antisense_methylation={}):
    """
    Summarise the methylation data across multiple regions.

    Parameters
        rdr: pyranges object
        regions_dict: dict

    Returns
        grouped_df: pd.DataFrame
    """
    # For each region in + strand expressed genes, summarise the methylation data
    for region, gr in regions_dict.items():
        rds_plus = plus_strand.reduce_byranges(
                    ranges=gr.unstrand(), 
                    var=["num_mc", "num_hmc", "num_modc", "num_total_c"]
                )
        
        rds_minus = minus_strand.reduce_byranges(
                ranges=gr.unstrand(), 
                var=["num_mc", "num_hmc", "num_modc", "num_total_c"]
            )
        
        if region_strand == "+":
            sense_plus_ds = rds_plus
            plus_sense = ['+'] * sense_plus_ds.dims['ranges']
            sense_plus_ds = sense_plus_ds.assign_coords(strand=('ranges', plus_sense))
        
            antisense_plus_ds = rds_minus
            plus_antisense = ['+'] * antisense_plus_ds.dims['ranges']
            antisense_plus_ds = antisense_plus_ds.assign_coords(strand=('ranges', plus_antisense))

            # Add the modified dataset to the dictionary
            if region not in sense_methylation:
                sense_methylation[region] = sense_plus_ds
                antisense_methylation[region] = antisense_plus_ds
            else:
                sense_methylation[region] = xr.concat([sense_methylation[region], sense_plus_ds], dim="ranges")
                antisense_methylation[region] = xr.concat([antisense_methylation[region], antisense_plus_ds], dim="ranges")
        else:
            antisense_minus_ds = rds_plus
            minus_antisense = ['-'] * antisense_minus_ds.dims['ranges']
            antisense_minus_ds = antisense_minus_ds.assign_coords(strand=('ranges', minus_antisense))
            
            sense_minus_ds = rds_minus
            minus_sense = ['-'] * sense_minus_ds.dims['ranges']
            sense_minus_ds = sense_minus_ds.assign_coords(strand=('ranges', minus_sense))

            # Add the modified dataset to the dictionary
            if region not in antisense_methylation:
                sense_methylation[region] = sense_minus_ds
                antisense_methylation[region] = antisense_minus_ds
            else:
                sense_methylation[region] = xr.concat([sense_methylation[region], sense_minus_ds], dim="ranges")
                antisense_methylation[region] = xr.concat([antisense_methylation[region], antisense_minus_ds], dim="ranges")


    return sense_methylation, antisense_methylation

In [34]:
sense_methylation, antisense_methylation = summarise_methylation_across_regions(plus_strand, minus_strand, dict_regions_to_patch_plus, "+")
sense_methylation, antisense_methylation = summarise_methylation_across_regions(plus_strand, minus_strand, dict_regions_to_patch_minus, "-", sense_methylation, antisense_methylation)

/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/xarray/core/utils.py:494: FutureWarning: The return type of `Dataset.dims` will be changed to return a set of dimension names in future, in order to be more consistent with `DataArray.dims`. To access a mapping from dimension names to lengths, please use `Dataset.sizes`.
  warnings.warn(
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/xarray/core/utils.py:494: FutureWarning: The return type of `Dataset.dims` will be changed to return a set of dimension names in future, in order to be more consistent with `DataArray.dims`. To access a mapping from dimension names to lengths, please use `Dataset.sizes`.
  warnings.warn(
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/xarray/core/utils.py:494: FutureWarning: The return type of `Dataset.dims` will be changed to return a set of dimension names in future, in order to be more consistent with `DataArray.dims`. To access a map

In [35]:
sense_methylation['exons']

<xarray.Dataset>
Dimensions:                   (ranges: 180974, sample_id: 1)
Coordinates:
    contig                    (ranges) <U2 '1' '1' '1' '1' ... 'Y' 'Y' 'Y' 'Y'
    start                     (ranges) int64 4808454 4828583 ... 89743993
    end                       (ranges) int64 4808485 4828648 ... 89744124
    range_id                  (ranges) int64 5 9 13 14 ... 408327 408328 408329
    num_contexts              (ranges) int64 1 0 0 0 0 2 2 0 ... 1 0 3 0 1 0 1 1
    range_length              (ranges) int64 31 65 65 47 47 ... 34 66 34 66 131
  * sample_id                 (sample_id) <U8 'sample_0'
    strand                    (ranges) <U1 '+' '+' '+' '+' ... '-' '-' '-' '-'
Dimensions without coordinates: ranges
Data variables:
    num_mc_sum                (ranges, sample_id) float64 0.0 0.0 ... 0.0 6.0
    num_mc_mean               (ranges, sample_id) float64 0.0 nan ... 0.0 6.0
    num_mc_cpg_count          (ranges, sample_id) float64 1.0 0.0 ... 1.0 1.0
    num_hmc_sum               (ranges, sample_id) float64 0.0 0.0 ... 0.0 0.0
    num_hmc_mean              (ranges, sample_id) float64 0.0 nan ... 0.0 0.0
    num_hmc_cpg_count         (ranges, sample_id) float64 1.0 0.0 ... 1.0 1.0
    num_modc_sum              (ranges, sample_id) float64 0.0 0.0 ... 0.0 6.0
    num_modc_mean             (ranges, sample_id) float64 0.0 nan ... 0.0 6.0
    num_modc_cpg_count        (ranges, sample_id) float64 1.0 0.0 ... 1.0 1.0
    num_total_c_sum           (ranges, sample_id) float64 113.0 0.0 ... 0.0 7.0
    num_total_c_mean          (ranges, sample_id) float64 113.0 nan ... 0.0 7.0
    num_total_c_cpg_count     (ranges, sample_id) float64 1.0 0.0 ... 1.0 1.0
    Source                    (ranges) object 'HAVANA' 'HAVANA' ... 'HAVANA'
    Type                      (ranges) object 'exon' 'exon' ... 'exon' 'exon'
    Score                     (ranges) object '.' '.' '.' '.' ... '.' '.' '.'
    Phase                     (ranges) object '.' '.' '.' '.' ... '.' '.' '.'
    Id                        (ranges) object 'exon:ENSMUST00000027036.10:2' ...
    Parent                    (ranges) object 'ENSMUST00000027036.10' ... 'EN...
    Gene_id                   (ranges) object 'ENSMUSG00000025903.14' ... 'EN...
    Transcript_id             (ranges) object 'ENSMUST00000027036.10' ... 'EN...
    Gene_type                 (ranges) object 'protein_coding' ... 'protein_c...
    Gene_name                 (ranges) object 'Lypla1' 'Lypla1' ... 'Gm21996'
    Transcript_type           (ranges) object 'protein_coding' ... 'protein_c...
    Transcript_name           (ranges) object 'Lypla1-201' ... 'Gm21996-201'
    Exon_number               (ranges) object '2' '3' '2' '4' ... '4' '3' '2'
    Exon_id                   (ranges) object 'ENSMUSE00001255376.1' ... 'ENS...
    Level                     (ranges) object '2' '2' '2' '2' ... '2' '2' '2'
    Transcript_support_level  (ranges) object '1' '1' '5' '1' ... '1' '1' '1'
    Mgi_id                    (ranges) object 'MGI:1344588' ... 'MGI:5440224'
    Tag                       (ranges) object 'basic,appris_principal_1,CCDS'...
    Havana_gene               (ranges) object 'OTTMUSG00000021562.4' ... 'OTT...
    Havana_transcript         (ranges) object 'OTTMUST00000051162.1' ... 'OTT...
    Protein_id                (ranges) object 'ENSMUSP00000027036.4' ... 'ENS...
    Ccdsid                    (ranges) object 'CCDS14806.1' 'CCDS14806.1' ... ''
    Ont                       (ranges) object '' '' '' '' '' ... '' '' '' '' ''

calculate methlyation fractions

In [36]:
dict_df_sense = {}
for region, gr in dict_regions_to_patch_plus.items():
    dict_df_sense[region] = summarise_across_region(sense_methylation[region], region)
stitched_sense_regions = pd.concat(dict_df_sense.values())

dict_df_antisense = {}
for region, gr in dict_regions_to_patch_minus.items():
    dict_df_antisense[region] = summarise_across_region(antisense_methylation[region], region)
stitched_antisense_regions = pd.concat(dict_df_antisense.values())


stitched_sense_regions.head()

/var/folders/gg/n2wtdbl13m54f9xcjyl_k3qr0000gp/T/ipykernel_97790/3351347453.py:4: RuntimeWarning: invalid value encountered in scalar divide
  return sum_var / sum_total_c
/var/folders/gg/n2wtdbl13m54f9xcjyl_k3qr0000gp/T/ipykernel_97790/3351347453.py:20: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  mean_mc = grouped.apply(get_mean_across_region, var="num_mc")
/var/folders/gg/n2wtdbl13m54f9xcjyl_k3qr0000gp/T/ipykernel_97790/3351347453.py:4: RuntimeWarning: invalid value encountered in scalar divide
  return sum_var / sum_total_c
/var/folders/gg/n2wtdbl13m54f9xcjyl_k3qr0000gp/T/ipykernel_97790/3351347453.py:21: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behav

Gene_id   mean_mc  mean_hmc  mean_modc  cpg_count  \
0   ENSMUSG00000000001.4  0.807449  0.025441   0.846691       51.0   
1  ENSMUSG00000000003.15  0.775309  0.014815   0.807407        7.0   
2  ENSMUSG00000000028.15  0.581154  0.031719   0.619681       60.0   
3  ENSMUSG00000000037.17  0.758958  0.017590   0.786971       33.0   
4  ENSMUSG00000000049.11  0.783202  0.036190   0.834756       28.0   

   range_length Gene_name contig strand          Transcript_id Region  
0          2995     Gnai3      3      -   ENSMUST00000000001.4  exons  
1           681      Pbsn      X      -  ENSMUST00000000003.13  exons  
2          1955     Cdc45     16      -  ENSMUST00000000028.13  exons  
3          2777     Scml2      X      +   ENSMUST00000101113.8  exons  
4          1068      Apoh     11      +   ENSMUST00000000049.5  exons

In [37]:
stitched_antisense_regions.head()

Gene_id   mean_mc  mean_hmc  mean_modc  cpg_count  \
0   ENSMUSG00000000001.4  0.810206  0.026502   0.848889       51.0   
1  ENSMUSG00000000003.15  0.746445  0.023697   0.779621        7.0   
2  ENSMUSG00000000028.15  0.557178  0.031306   0.597080       60.0   
3  ENSMUSG00000000037.17  0.765890  0.014475   0.791064       33.0   
4  ENSMUSG00000000049.11  0.794449  0.026632   0.834209       28.0   

   range_length Gene_name contig strand          Transcript_id Region  
0          2995     Gnai3      3      -   ENSMUST00000000001.4  exons  
1           681      Pbsn      X      -  ENSMUST00000000003.13  exons  
2          1955     Cdc45     16      -  ENSMUST00000000028.13  exons  
3          2777     Scml2      X      +   ENSMUST00000101113.8  exons  
4          1068      Apoh     11      +   ENSMUST00000000049.5  exons

### no stitching

#### TSS, TES, first exon, first intron

In [38]:
print(f"plus strand total regions: {len(before_tss_plus)+ len(after_tes_plus) + len(genes_clean) + len(first_exons_plus) + len(first_introns_plus)}")
print(f"minus strand total regions: {len(before_tss_minus)+ len(after_tes_minus) + len(genes_clean) + len(first_exons_minus) + len(first_introns_minus)}")

plus strand total regions: 63947
minus strand total regions: 64156


In [40]:
#drop columns
to_drop = ["Score", "Source", "Phase", "Type"]

regions_dict_plus ={
        "before_tss": before_tss_plus,
        "after_tes": after_tes_plus,
        "genes": genes_clean,
        "first_exons": first_exons_plus,
        "first_introns": first_introns_plus,
    }

for region in regions_dict_plus:
    regions_dict_plus[region].Region = region
    try:
        regions_dict_plus[region] = regions_dict_plus[region].drop(to_drop)
    except:
        pass

regions_dict_minus ={
        "before_tss": before_tss_minus,
        "after_tes": after_tes_minus,
        "genes": genes_clean,
        "first_exons": first_exons_minus,
        "first_introns": first_introns_minus,
    }

for region in regions_dict_minus:
    regions_dict_minus[region].Region = region
    try:
        regions_dict_minus[region] = regions_dict_minus[region].drop(to_drop)
    except:
        pass


In [81]:
def summarise_methylation_across_other_regions(plus_strand_cpgs, minus_strand_cpgs, regions_dict, strand, sense_methylation=None, antisense_methylation=None):
    """
    Summarise the methylation data across multiple regions.

    Parameters
        rdr: pyranges object
        regions_dict: dict

    Returns
        grouped_df: pd.DataFrame
    """

    rds_plus = plus_strand_cpgs.reduce_byranges(
                ranges=list(regions_dict.values()), 
                var=["num_mc", "num_hmc", "num_modc", "num_total_c"]
            )
    rds_minus = minus_strand_cpgs.reduce_byranges(
                ranges=list(regions_dict.values()),      
                var=["num_mc", "num_hmc", "num_modc", "num_total_c"]
            )

    if strand == "+":
        sense_plus_ds = rds_plus
        plus_sense = ['+'] * sense_plus_ds.dims['ranges']
        sense_plus_ds = sense_plus_ds.assign_coords(strand=('ranges', plus_sense))
    
        antisense_plus_ds = rds_minus
        plus_antisense = ['+'] * antisense_plus_ds.dims['ranges']
        antisense_plus_ds = antisense_plus_ds.assign_coords(strand=('ranges', plus_antisense))

        # Add the modified dataset to the dictionary
        if sense_methylation is None:
            sense_methylation= sense_plus_ds
            antisense_methylation= antisense_plus_ds
        else:
            # print("hi:" ,sense_methylation)
            sense_methylation= xr.concat([sense_methylation, sense_plus_ds], dim="ranges")
            antisense_methylation= xr.concat([antisense_methylation, antisense_plus_ds], dim="ranges")
    else:
        antisense_minus_ds = rds_plus
        minus_antisense = ['-'] * antisense_minus_ds.dims['ranges']
        antisense_minus_ds = antisense_minus_ds.assign_coords(strand=('ranges', minus_antisense))
        
        sense_minus_ds = rds_minus
        minus_sense = ['-'] * sense_minus_ds.dims['ranges']
        sense_minus_ds = sense_minus_ds.assign_coords(strand=('ranges', minus_sense))

        # Add the modified dataset to the dictionary
        if antisense_methylation is None:
            sense_methylation = sense_minus_ds
            antisense_methylation= antisense_minus_ds
        else:
            sense_methylation = xr.concat([sense_methylation, sense_minus_ds], dim="ranges")
            antisense_methylation = xr.concat([antisense_methylation, antisense_minus_ds], dim="ranges")


    return sense_methylation, antisense_methylation

In [85]:
sense_ds, antisense_ds = summarise_methylation_across_other_regions(plus_strand, minus_strand, regions_dict_plus, "+")
sense_ds, antisense_ds = summarise_methylation_across_other_regions(plus_strand, minus_strand, regions_dict_minus, "-", sense_ds, antisense_ds)

/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:162: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  empty_removed = df.groupby("Chromosome")
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:162: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  empty_removed = df.groupby("Chromosome")
/Users/nicolawong/miniforge3/envs/modality/lib/python3.11/site-packages/pyranges/methods/init.py:45: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False

In [89]:
# Compute mean methylation levels as mc / total_c
sense_ds = sense_ds.assign(
    mean_mc = sense_ds["num_mc_sum"] / sense_ds["num_total_c_sum"],
    mean_hmc = sense_ds["num_hmc_sum"] / sense_ds["num_total_c_sum"],
    mean_modc = sense_ds["num_modc_sum"] / sense_ds["num_total_c_sum"],
)
sense_ds

<xarray.Dataset>
Dimensions:                   (ranges: 128103, sample_id: 1)
Coordinates:
    contig                    (ranges) <U2 '1' '1' '1' '1' ... 'Y' 'Y' 'Y' 'Y'
    start                     (ranges) int64 4807587 4807691 ... 22859847
    end                       (ranges) int64 4807787 4807891 ... 22861212
    range_id                  (ranges) int64 0 1 2 3 ... 64152 64153 64154 64155
    num_contexts              (ranges) int64 27 23 21 0 7 0 ... 10 12 10 9 11 10
    range_length              (ranges) int64 200 200 200 200 ... 1361 1365 1365
  * sample_id                 (sample_id) <U8 'sample_0'
    strand                    (ranges) <U1 '+' '+' '+' '+' ... '-' '-' '-' '-'
Dimensions without coordinates: ranges
Data variables:
    num_mc_sum                (ranges, sample_id) float64 0.0 1.0 ... 0.0 0.0
    num_mc_mean               (ranges, sample_id) float64 0.0 0.04348 ... 0.0
    num_mc_cpg_count          (ranges, sample_id) float64 27.0 23.0 ... 10.0
    num_hmc_sum               (ranges, sample_id) float64 1.0 1.0 ... 0.0 0.0
    num_hmc_mean              (ranges, sample_id) float64 0.03704 ... 0.0
    num_hmc_cpg_count         (ranges, sample_id) float64 27.0 23.0 ... 10.0
    num_modc_sum              (ranges, sample_id) float64 1.0 2.0 ... 0.0 0.0
    num_modc_mean             (ranges, sample_id) float64 0.03704 ... 0.0
    num_modc_cpg_count        (ranges, sample_id) float64 27.0 23.0 ... 10.0
    num_total_c_sum           (ranges, sample_id) float64 2.122e+03 ... 0.0
    num_total_c_mean          (ranges, sample_id) float64 78.59 81.22 ... 0.0
    num_total_c_cpg_count     (ranges, sample_id) float64 27.0 23.0 ... 10.0
    Id                        (ranges) object 'ENSMUSG00000025903.14' ... 'EN...
    Gene_id                   (ranges) object 'ENSMUSG00000025903.14' ... 'EN...
    Gene_type                 (ranges) object 'protein_coding' ... 'protein_c...
    Gene_name                 (ranges) object 'Lypla1' 'Gm37988' ... 'Gm21366'
    Level                     (ranges) object '2' '2' '2' '2' ... '2' '2' '2'
    Mgi_id                    (ranges) object 'MGI:1344588' ... 'MGI:5434721'
    Havana_gene               (ranges) object 'OTTMUSG00000021562.4' ... 'OTT...
    Tag                       (ranges) object 'overlapping_locus' ... ''
    Transcript_id             (ranges) object 'ENSMUST00000027036.10' ... 'EN...
    Region                    (ranges) object 'before_tss' ... 'first_introns'
    Strand                    (ranges) object '.' '.' '.' '.' ... '.' '.' '.'
    Parent                    (ranges) object nan nan nan nan ... nan nan nan
    Transcript_type           (ranges) object nan nan nan nan ... nan nan nan
    Transcript_name           (ranges) object nan nan nan nan ... nan nan nan
    Exon_number               (ranges) object nan nan nan nan ... nan nan nan
    Exon_id                   (ranges) object nan nan nan nan ... nan nan nan
    Transcript_support_level  (ranges) object nan nan nan nan ... nan nan nan
    Havana_transcript         (ranges) object nan nan nan nan ... nan nan nan
    Protein_id                (ranges) object nan nan nan nan ... nan nan nan
    Ccdsid                    (ranges) object nan nan nan nan ... nan nan nan
    Ont                       (ranges) object nan nan nan nan ... nan nan nan
    Level_1                   (ranges) float64 nan nan nan nan ... 8.0 8.0 8.0
    Ranges_id                 (ranges) float64 nan nan ... 2.164e+04 2.164e+04
    Intron_number             (ranges) object nan nan nan nan ... '1' '1' '1'
    mean_mc                   (ranges, sample_id) float64 0.0 0.0005353 ... nan
    mean_hmc                  (ranges, sample_id) float64 0.0004713 ... nan
    mean_modc                 (ranges, sample_id) float64 0.0004713 ... nan

In [90]:
antisense_ds = antisense_ds.assign(
    mean_mc = antisense_ds["num_mc_sum"] / antisense_ds["num_total_c_sum"],
    mean_hmc = antisense_ds["num_hmc_sum"] / antisense_ds["num_total_c_sum"],
    mean_modc = antisense_ds["num_modc_sum"] / antisense_ds["num_total_c_sum"],
)
antisense_ds

<xarray.Dataset>
Dimensions:                   (ranges: 128103, sample_id: 1)
Coordinates:
    contig                    (ranges) <U2 '1' '1' '1' '1' ... 'Y' 'Y' 'Y' 'Y'
    start                     (ranges) int64 4807587 4807691 ... 22859847
    end                       (ranges) int64 4807787 4807891 ... 22861212
    range_id                  (ranges) int64 0 1 2 3 ... 64152 64153 64154 64155
    num_contexts              (ranges) int64 27 23 22 0 7 0 ... 10 12 10 9 11 10
    range_length              (ranges) int64 200 200 200 200 ... 1361 1365 1365
  * sample_id                 (sample_id) <U8 'sample_0'
    strand                    (ranges) <U1 '+' '+' '+' '+' ... '-' '-' '-' '-'
Dimensions without coordinates: ranges
Data variables:
    num_mc_sum                (ranges, sample_id) float64 1.0 1.0 ... 0.0 0.0
    num_mc_mean               (ranges, sample_id) float64 0.03704 ... 0.0
    num_mc_cpg_count          (ranges, sample_id) float64 27.0 23.0 ... 10.0
    num_hmc_sum               (ranges, sample_id) float64 3.0 3.0 ... 0.0 0.0
    num_hmc_mean              (ranges, sample_id) float64 0.1111 0.1304 ... 0.0
    num_hmc_cpg_count         (ranges, sample_id) float64 27.0 23.0 ... 10.0
    num_modc_sum              (ranges, sample_id) float64 4.0 4.0 ... 0.0 0.0
    num_modc_mean             (ranges, sample_id) float64 0.1481 0.1739 ... 0.0
    num_modc_cpg_count        (ranges, sample_id) float64 27.0 23.0 ... 10.0
    num_total_c_sum           (ranges, sample_id) float64 2.111e+03 ... 0.0
    num_total_c_mean          (ranges, sample_id) float64 78.19 71.96 ... 0.0
    num_total_c_cpg_count     (ranges, sample_id) float64 27.0 23.0 ... 10.0
    Id                        (ranges) object 'ENSMUSG00000025903.14' ... 'EN...
    Gene_id                   (ranges) object 'ENSMUSG00000025903.14' ... 'EN...
    Gene_type                 (ranges) object 'protein_coding' ... 'protein_c...
    Gene_name                 (ranges) object 'Lypla1' 'Gm37988' ... 'Gm21366'
    Level                     (ranges) object '2' '2' '2' '2' ... '2' '2' '2'
    Mgi_id                    (ranges) object 'MGI:1344588' ... 'MGI:5434721'
    Havana_gene               (ranges) object 'OTTMUSG00000021562.4' ... 'OTT...
    Tag                       (ranges) object 'overlapping_locus' ... ''
    Transcript_id             (ranges) object 'ENSMUST00000027036.10' ... 'EN...
    Region                    (ranges) object 'before_tss' ... 'first_introns'
    Strand                    (ranges) object '.' '.' '.' '.' ... '.' '.' '.'
    Parent                    (ranges) object nan nan nan nan ... nan nan nan
    Transcript_type           (ranges) object nan nan nan nan ... nan nan nan
    Transcript_name           (ranges) object nan nan nan nan ... nan nan nan
    Exon_number               (ranges) object nan nan nan nan ... nan nan nan
    Exon_id                   (ranges) object nan nan nan nan ... nan nan nan
    Transcript_support_level  (ranges) object nan nan nan nan ... nan nan nan
    Havana_transcript         (ranges) object nan nan nan nan ... nan nan nan
    Protein_id                (ranges) object nan nan nan nan ... nan nan nan
    Ccdsid                    (ranges) object nan nan nan nan ... nan nan nan
    Ont                       (ranges) object nan nan nan nan ... nan nan nan
    Level_1                   (ranges) float64 nan nan nan nan ... 8.0 8.0 8.0
    Ranges_id                 (ranges) float64 nan nan ... 2.164e+04 2.164e+04
    Intron_number             (ranges) object nan nan nan nan ... '1' '1' '1'
    mean_mc                   (ranges, sample_id) float64 0.0004737 ... nan
    mean_hmc                  (ranges, sample_id) float64 0.001421 ... nan
    mean_modc                 (ranges, sample_id) float64 0.001895 ... nan

In [91]:
missing_transcript_genes = sense_ds["Transcript_id"].where(sense_ds["Transcript_id"].isnull(), drop=True)
if len(missing_transcript_genes) > 0:
    print("SENSE Gene IDs with missing Transcript IDs:")
    print(missing_transcript_genes)

missing_transcript_genes = antisense_ds["Transcript_id"].where(antisense_ds["Transcript_id"].isnull(), drop=True)
if len(missing_transcript_genes) > 0:
    print("ANTISENSE Gene IDs with missing Transcript IDs:")
    print(missing_transcript_genes)

### Combine features

exon introns 3\`UTRs 5\`UTRs

In [97]:
stitched_sense_regions['Sense'] = "sense"
stitched_antisense_regions['Sense'] = "antisense"

stitched_regions = pd.concat([stitched_sense_regions, stitched_antisense_regions])
stitched_sense_regions

Gene_id   mean_mc  mean_hmc  mean_modc  cpg_count  \
0       ENSMUSG00000000001.4  0.807449  0.025441   0.846691       51.0   
1      ENSMUSG00000000003.15  0.775309  0.014815   0.807407        7.0   
2      ENSMUSG00000000028.15  0.581154  0.031719   0.619681       60.0   
3      ENSMUSG00000000037.17  0.758958  0.017590   0.786971       33.0   
4      ENSMUSG00000000049.11  0.783202  0.036190   0.834756       28.0   
...                      ...       ...       ...        ...        ...   
15461   ENSMUSG00000118219.1  0.429907  0.084696   0.524143       53.0   
15462   ENSMUSG00000118332.1  0.794369  0.041759   0.847517       37.0   
15463   ENSMUSG00000118346.1       NaN       NaN        NaN        0.0   
15464   ENSMUSG00000118537.1  0.735043  0.025641   0.786325        1.0   
15465   ENSMUSG00000118560.1  0.508197  0.049180   0.573770        2.0   

       range_length Gene_name contig strand          Transcript_id  \
0              2995     Gnai3      3      -   ENSMUST00000000001.4   
1               681      Pbsn      X      -  ENSMUST00000000003.13   
2              1955     Cdc45     16      -  ENSMUST00000000028.13   
3              2777     Scml2      X      +   ENSMUST00000101113.8   
4              1068      Apoh     11      +   ENSMUST00000000049.5   
...             ...       ...    ...    ...                    ...   
15461          5100   Gm29695      1      +   ENSMUST00000188175.1   
15462          1753   Fam220a      5      +   ENSMUST00000119488.1   
15463           120  Tmem179b     19      -   ENSMUST00000010249.6   
15464           411     Shld3     13      -   ENSMUST00000133280.1   
15465           286      Lim2      7      +   ENSMUST00000004732.6   

                 Region  Sense  
0                 exons  sense  
1                 exons  sense  
2                 exons  sense  
3                 exons  sense  
4                 exons  sense  
...                 ...    ...  
15461  three_prime_utrs  sense  
15462  three_prime_utrs  sense  
15463  three_prime_utrs  sense  
15464  three_prime_utrs  sense  
15465  three_prime_utrs  sense  

[69769 rows x 12 columns]

TSS TES

In [98]:
df_sense = sense_ds.to_dataframe().reset_index(level="sample_id", drop=True)
df_antisense = antisense_ds.to_dataframe().reset_index(level="sample_id", drop=True)

df_sense["Sense"] = "sense"
df_antisense["Sense"] = "antisense"
df = pd.concat([df_sense, df_antisense])
df

num_mc_sum  num_mc_mean  num_mc_cpg_count  num_hmc_sum  num_hmc_mean  \
ranges                                                                         
0              0.0     0.000000              27.0          1.0      0.037037   
1              1.0     0.043478              23.0          1.0      0.043478   
2              4.0     0.190476              21.0          2.0      0.095238   
3              0.0          NaN               0.0          0.0           NaN   
4            136.0    19.428571               7.0         23.0      3.285714   
...            ...          ...               ...          ...           ...   
128098         0.0     0.000000              12.0          0.0      0.000000   
128099         8.0     0.800000              10.0          0.0      0.000000   
128100        22.0     2.444444               9.0          1.0      0.111111   
128101         0.0     0.000000              11.0          0.0      0.000000   
128102         0.0     0.000000              10.0          0.0      0.000000   

        num_hmc_cpg_count  num_modc_sum  num_modc_mean  num_modc_cpg_count  \
ranges                                                                       
0                    27.0           1.0       0.037037                27.0   
1                    23.0           2.0       0.086957                23.0   
2                    21.0           6.0       0.285714                21.0   
3                     0.0           0.0            NaN                 0.0   
4                     7.0         159.0      22.714286                 7.0   
...                   ...           ...            ...                 ...   
128098               12.0           0.0       0.000000                12.0   
128099               10.0           8.0       0.800000                10.0   
128100                9.0          24.0       2.666667                 9.0   
128101               11.0           0.0       0.000000                11.0   
128102               10.0           0.0       0.000000                10.0   

        num_total_c_sum  ...  Ccdsid  Ont Level_1  Ranges_id  Intron_number  \
ranges                   ...                                                  
0                2122.0  ...     NaN  NaN     NaN        NaN            NaN   
1                1868.0  ...     NaN  NaN     NaN        NaN            NaN   
2                2032.0  ...     NaN  NaN     NaN        NaN            NaN   
3                   0.0  ...     NaN  NaN     NaN        NaN            NaN   
4                 501.0  ...     NaN  NaN     NaN        NaN            NaN   
...                 ...  ...     ...  ...     ...        ...            ...   
128098              0.0  ...     NaN  NaN     8.0    21666.0              1   
128099              8.0  ...     NaN  NaN     8.0    21650.0              1   
128100             32.0  ...     NaN  NaN     8.0    21635.0              1   
128101              0.0  ...     NaN  NaN     8.0    21636.0              1   
128102              0.0  ...     NaN  NaN     8.0    21637.0              1   

        strand   mean_mc  mean_hmc mean_modc      Sense  
ranges                                                   
0            +  0.000000  0.000471  0.000471      sense  
1            +  0.000535  0.000535  0.001071      sense  
2            +  0.001969  0.000984  0.002953      sense  
3            +       NaN       NaN       NaN      sense  
4            +  0.271457  0.045908  0.317365      sense  
...        ...       ...       ...       ...        ...  
128098       -       NaN       NaN       NaN  antisense  
128099       -  1.000000  0.000000  1.000000  antisense  
128100       -  0.687500  0.031250  0.750000  antisense  
128101       -       NaN       NaN       NaN  antisense  
128102       -       NaN       NaN       NaN  antisense  

[256206 rows x 47 columns]

In [103]:
df["cpg_count"] = df["num_total_c_cpg_count"]
df=df[stitched_regions.columns].reset_index(drop=True)
df = pd.concat([df, stitched_regions]).reset_index(drop=True)
df

Gene_id   mean_mc  mean_hmc  mean_modc  cpg_count  \
0       ENSMUSG00000025903.14  0.000000  0.000471   0.000471       27.0   
1        ENSMUSG00000104217.1  0.000535  0.000535   0.001071       23.0   
2       ENSMUSG00000033813.15  0.001969  0.000984   0.002953       21.0   
3       ENSMUSG00000033793.12       NaN       NaN        NaN        0.0   
4       ENSMUSG00000025905.14  0.271457  0.045908   0.317365        7.0   
...                       ...       ...       ...        ...        ...   
395739   ENSMUSG00000118219.1  0.418332  0.083410   0.508708       53.0   
395740   ENSMUSG00000118332.1  0.813510  0.045612   0.870958       37.0   
395741   ENSMUSG00000118346.1       NaN       NaN        NaN        0.0   
395742   ENSMUSG00000118537.1  0.766355  0.009346   0.813084        1.0   
395743   ENSMUSG00000118560.1  0.607843  0.078431   0.699346        2.0   

        range_length Gene_name contig strand          Transcript_id  \
0                200    Lypla1      1      +  ENSMUST00000027036.10   
1                200   Gm37988      1      +   ENSMUST00000155020.1   
2                200     Tcea1      1      +  ENSMUST00000081551.13   
3                200   Atp6v1h      1      +   ENSMUST00000192847.5   
4                200     Oprk1      1      +   ENSMUST00000160777.7   
...              ...       ...    ...    ...                    ...   
395739          5100   Gm29695      1      +   ENSMUST00000188175.1   
395740          1753   Fam220a      5      +   ENSMUST00000119488.1   
395741           120  Tmem179b     19      -   ENSMUST00000010249.6   
395742           411     Shld3     13      -   ENSMUST00000133280.1   
395743           286      Lim2      7      +   ENSMUST00000004732.6   

                  Region      Sense  
0             before_tss      sense  
1             before_tss      sense  
2             before_tss      sense  
3             before_tss      sense  
4             before_tss      sense  
...                  ...        ...  
395739  three_prime_utrs  antisense  
395740  three_prime_utrs  antisense  
395741  three_prime_utrs  antisense  
395742  three_prime_utrs  antisense  
395743  three_prime_utrs  antisense  

[395744 rows x 12 columns]

pivot table

In [104]:
df_pivot = df.pivot(
    index=["Gene_id", "Gene_name", "contig", "strand"],
    # index = ["Transcript_id", "contig", "strand"],
    columns=["Region", "Sense"],
    values=["mean_mc", "mean_hmc", "mean_modc", "cpg_count", "range_length"],
)

In [105]:
df_pivot

mean_mc                      \
Region                                         before_tss after_tes     genes   
Sense                                               sense     sense     sense   
Gene_id               Gene_name  contig strand                                  
ENSMUSG00000000001.4  Gnai3      3      +             NaN       NaN  0.642745   
                                        -        0.000000  0.000000  0.643948   
ENSMUSG00000000003.15 Pbsn       X      +             NaN       NaN  0.739106   
                                        -             NaN       NaN  0.743048   
ENSMUSG00000000028.15 Cdc45      16     +             NaN       NaN  0.633455   
...                                                   ...       ...       ...   
ENSMUSG00000118640.1  AC167036.2 1      -        0.851459  0.851459  0.780381   
ENSMUSG00000118646.1  AC160405.1 10     +             NaN       NaN  0.765643   
                                        -        0.833333  0.833333  0.761150   
ENSMUSG00000118653.1  AC159819.1 9      +        0.278552  0.278552  0.280672   
                                        -             NaN       NaN  0.300631   

                                                                          \
Region                                         first_exons first_introns   
Sense                                                sense         sense   
Gene_id               Gene_name  contig strand                             
ENSMUSG00000000001.4  Gnai3      3      +              NaN           NaN   
                                        -         0.000455      0.585086   
ENSMUSG00000000003.15 Pbsn       X      +              NaN           NaN   
                                        -         0.719298      0.733333   
ENSMUSG00000000028.15 Cdc45      16     +              NaN           NaN   
...                                                    ...           ...   
ENSMUSG00000118640.1  AC167036.2 1      -         0.780381           NaN   
ENSMUSG00000118646.1  AC160405.1 10     +              NaN           NaN   
                                        -         0.777778      0.759917   
ENSMUSG00000118653.1  AC159819.1 9      +         0.280672           NaN   
                                        -              NaN           NaN   

                                                                               \
Region                                         before_tss after_tes     genes   
Sense                                           antisense antisense antisense   
Gene_id               Gene_name  contig strand                                  
ENSMUSG00000000001.4  Gnai3      3      +             NaN       NaN  0.643948   
                                        -        0.001415  0.001415  0.642745   
ENSMUSG00000000003.15 Pbsn       X      +             NaN       NaN  0.743048   
                                        -             NaN       NaN  0.739106   
ENSMUSG00000000028.15 Cdc45      16     +             NaN       NaN  0.646144   
...                                                   ...       ...       ...   
ENSMUSG00000118640.1  AC167036.2 1      -        0.867500  0.867500  0.810038   
ENSMUSG00000118646.1  AC160405.1 10     +             NaN       NaN  0.761150   
                                        -        0.860000  0.860000  0.765643   
ENSMUSG00000118653.1  AC159819.1 9      +        0.315934  0.315934  0.300631   
                                        -             NaN       NaN  0.280672   

                                                                          ...  \
Region                                         first_exons first_introns  ...   
Sense                                            antisense     antisense  ...   
Gene_id               Gene_name  contig strand                            ...   
ENSMUSG00000000001.4  Gnai3      3      +              NaN           NaN  ...   
                                        -         0.000000      0.577560

In [116]:
# compost feature names
df_features = df_pivot.copy()
df_features.columns = [" ".join(col).strip() for col in df_features.columns.values]
features = df_features.columns
features = [f.replace(" ", "_") for f in features]
df_features.columns = features
df_features

mean_mc_before_tss_sense  \
Gene_id               Gene_name  contig strand                             
ENSMUSG00000000001.4  Gnai3      3      +                            NaN   
                                        -                       0.000000   
ENSMUSG00000000003.15 Pbsn       X      +                            NaN   
                                        -                            NaN   
ENSMUSG00000000028.15 Cdc45      16     +                            NaN   
...                                                                  ...   
ENSMUSG00000118640.1  AC167036.2 1      -                       0.851459   
ENSMUSG00000118646.1  AC160405.1 10     +                            NaN   
                                        -                       0.833333   
ENSMUSG00000118653.1  AC159819.1 9      +                       0.278552   
                                        -                            NaN   

                                                mean_mc_after_tes_sense  \
Gene_id               Gene_name  contig strand                            
ENSMUSG00000000001.4  Gnai3      3      +                           NaN   
                                        -                      0.000000   
ENSMUSG00000000003.15 Pbsn       X      +                           NaN   
                                        -                           NaN   
ENSMUSG00000000028.15 Cdc45      16     +                           NaN   
...                                                                 ...   
ENSMUSG00000118640.1  AC167036.2 1      -                      0.851459   
ENSMUSG00000118646.1  AC160405.1 10     +                           NaN   
                                        -                      0.833333   
ENSMUSG00000118653.1  AC159819.1 9      +                      0.278552   
                                        -                           NaN   

                                                mean_mc_genes_sense  \
Gene_id               Gene_name  contig strand                        
ENSMUSG00000000001.4  Gnai3      3      +                  0.642745   
                                        -                  0.643948   
ENSMUSG00000000003.15 Pbsn       X      +                  0.739106   
                                        -                  0.743048   
ENSMUSG00000000028.15 Cdc45      16     +                  0.633455   
...                                                             ...   
ENSMUSG00000118640.1  AC167036.2 1      -                  0.780381   
ENSMUSG00000118646.1  AC160405.1 10     +                  0.765643   
                                        -                  0.761150   
ENSMUSG00000118653.1  AC159819.1 9      +                  0.280672   
                                        -                  0.300631   

                                                mean_mc_first_exons_sense  \
Gene_id               Gene_name  contig strand                              
ENSMUSG00000000001.4  Gnai3      3      +                             NaN   
                                        -                        0.000455   
ENSMUSG00000000003.15 Pbsn       X      +                             NaN   
                                        -                        0.719298   
ENSMUSG00000000028.15 Cdc45      16     +                             NaN   
...                                                                   ...   
ENSMUSG00000118640.1  AC167036.2 1      -                        0.780381   
ENSMUSG00000118646.1  AC160405.1 10     +                             NaN   
                                        -                        0.777778   
ENSMUSG00000118653.1  AC159819.1 9      +                        0.280672   
                                        -                             NaN   

                                                mean_mc_first_introns_sense  \
Gene_id               Gene_name  contig strand                                

### write to file

Finally, we write this feature file as a pickle file, which preserves the variable type, and is therefore prefered over a more basic text file.

In [117]:
df_features = df_features.reset_index()
# add a column with a boolean depending on whether the transcript is is selected_transcripts or not
df_features["selected_transcript"] = df_features.Gene_id.isin(selected_transcripts.gene_id)
df_features.columns

Index(['Gene_id', 'Gene_name', 'contig', 'strand', 'mean_mc_before_tss_sense',
       'mean_mc_after_tes_sense', 'mean_mc_genes_sense',
       'mean_mc_first_exons_sense', 'mean_mc_first_introns_sense',
       'mean_mc_before_tss_antisense', 'mean_mc_after_tes_antisense',
       'mean_mc_genes_antisense', 'mean_mc_first_exons_antisense',
       'mean_mc_first_introns_antisense', 'mean_mc_exons_sense',
       'mean_mc_introns_sense', 'mean_mc_five_prime_utrs_sense',
       'mean_mc_three_prime_utrs_sense', 'mean_mc_exons_antisense',
       'mean_mc_introns_antisense', 'mean_mc_five_prime_utrs_antisense',
       'mean_mc_three_prime_utrs_antisense', 'mean_hmc_before_tss_sense',
       'mean_hmc_after_tes_sense', 'mean_hmc_genes_sense',
       'mean_hmc_first_exons_sense', 'mean_hmc_first_introns_sense',
       'mean_hmc_before_tss_antisense', 'mean_hmc_after_tes_antisense',
       'mean_hmc_genes_antisense', 'mean_hmc_first_exons_antisense',
       'mean_hmc_first_introns_antisense', 'me

In [118]:
genes.df.columns

Index(['Chromosome', 'Source', 'Type', 'Start', 'End', 'Score', 'Strand',
       'Phase', 'Id', 'Gene_id', 'Gene_type', 'Gene_name', 'Level', 'Mgi_id',
       'Havana_gene', 'Tag', 'Ranges_ID'],
      dtype='object')

In [119]:
df_features = genes.df[["Gene_id", "Chromosome", "Start", "End"]].merge(
    df_features, on="Gene_id", how="left",
    )
df_features

Gene_id Chromosome     Start       End Gene_name contig  \
0      ENSMUSG00000025903.14          1   4807787   4848409    Lypla1      1   
1      ENSMUSG00000025903.14          1   4807787   4848409    Lypla1      1   
2       ENSMUSG00000104217.1          1   4807891   4886769   Gm37988      1   
3       ENSMUSG00000104217.1          1   4807891   4886769   Gm37988      1   
4      ENSMUSG00000033813.15          1   4857813   4897908     Tcea1      1   
...                      ...        ...       ...       ...       ...    ...   
43209   ENSMUSG00000094660.2          Y  84562571  84564906   Gm21394      Y   
43210   ENSMUSG00000095650.2          Y  85528516  85530907   Gm20854      Y   
43211   ENSMUSG00000095650.2          Y  85528516  85530907   Gm20854      Y   
43212   ENSMUSG00000100608.1          Y  89713423  89745531   Gm21996      Y   
43213   ENSMUSG00000100608.1          Y  89713423  89745531   Gm21996      Y   

      strand  mean_mc_before_tss_sense  mean_mc_after_tes_sense  \
0          +                  0.000000                 0.000000   
1          -                       NaN                      NaN   
2          +                  0.000535                 0.000535   
3          -                       NaN                      NaN   
4          +                  0.001969                 0.001969   
...      ...                       ...                      ...   
43209      -                       NaN                      NaN   
43210      +                       NaN                      NaN   
43211      -                       NaN                      NaN   
43212      +                       NaN                      NaN   
43213      -                  0.800000                 0.800000   

       mean_mc_genes_sense  ...  range_length_first_introns_antisense  \
0                 0.486957  ...                                  35.0   
1                 0.498660  ...                                   NaN   
2                 0.391258  ...                               20602.0   
3                 0.405710  ...                                   NaN   
4                 0.442052  ...                                9494.0   
...                    ...  ...                                   ...   
43209             0.683544  ...                                1114.0   
43210             0.617647  ...                                   NaN   
43211             0.642857  ...                                1231.0   
43212             0.690289  ...                                   NaN   
43213             0.766404  ...                                1364.0   

       range_length_exons_sense  range_length_introns_sense  \
0                        2339.0                     38089.0   
1                           NaN                         NaN   
2                         725.0                     57461.0   
3                           NaN                         NaN   
4                        2375.0                     28064.0   
...                         ...                         ...   
43209                    1103.0                         NaN   
43210                       NaN                         NaN   
43211                    1101.0                         6.0   
43212                       NaN                         NaN   
43213                     878.0                     29823.0   

       range_length_five_prime_utrs_sense  \
0                                    90.0   
1                                     NaN   
2                                     NaN   
3                                     NaN   
4                                    99.0   
...                                   ...   
43209                               398.0   
43210                                 NaN   
43211                                 NaN   
43212                                 NaN   
43213                                56.0   

       range_length_three_prime_utrs_sense  range_length_exons_antisense  \
0   

In [120]:
df_features.to_pickle("nic_features.pickle")